In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt



from datetime import datetime,timedelta

from xgboost import XGBClassifier

In [2]:
news_data = pd.read_csv('news_categ.csv')
news_data = news_data.iloc[:,1:]
news_data.head(5)

0         1         2         3         4         5         6  \
0  0.000035  0.000314  0.000140  0.000070  0.000070  0.000140  0.000140   
1  0.000070  0.000070  0.000140  0.000175  0.000035  0.000070  0.000314   
2  0.000070  0.000175  0.000105  0.000070  0.000000  0.000105  0.000070   
3  0.000035  0.000140  0.000000  0.000070  0.000210  0.000035  0.000070   
4  0.000140  0.000035  0.000244  0.000070  0.000105  0.000105  0.000140   

          7         8         9        10        11        12        13  \
0  0.000210  0.000140  0.000140  0.000210  0.000105  0.000105  0.000000   
1  0.000175  0.000175  0.000000  0.000210  0.000070  0.000105  0.000070   
2  0.000070  0.000035  0.000035  0.000105  0.000105  0.000070  0.000070   
3  0.000000  0.000140  0.000140  0.000105  0.000000  0.000244  0.000035   
4  0.000140  0.000105  0.000244  0.000105  0.000105  0.000175  0.000070   

         14        15        16          17  
0  0.000140  0.000000  0.000559  2019-06-01  
1  0.000175  0.000210  0.000140  2020-01-06  
2  0.000140  0.000210  0.000210  2019-12-29  
3  0.000140  0.000105  0.000175  2019-12-15  
4  0.000035  0.000070  0.000244  2019-08-13

In [3]:
stock_data = pd.read_excel('Stock_data.xlsx')
stock_data.head()

Dates  PX_HIGH  PX_CLOSE_1D  PX_VOLUME   PX_LOW  PX_OPEN  Unnamed: 6
0 2010-01-04  5238.45      5201.05  148652400  5167.10  5200.90     5200.00
1 2010-01-05  5288.35      5232.20  240844400  5242.40  5277.15     5200.90
2 2010-01-06  5310.85      5277.90  216147800  5260.05  5278.15     5277.15
3 2010-01-07  5302.55      5281.80  181246700  5244.75  5281.80     5278.15
4 2010-01-08  5276.75      5263.10  201910800  5234.70  5264.25     5281.80

In [4]:
#stock_data = stock_data.iloc[:,[0,1,2,5]]

### Ensuring the formatting of Date column is same for both Dataframes

In [5]:
for i in range(news_data.shape[0]):
    news_data.iloc[i,-1] = datetime.strptime(news_data.iloc[i,-1], '%Y-%m-%d').strftime('%m/%d/%y')

In [6]:
for i in range(stock_data.shape[0]):
    stock_data.iloc[i,0] = datetime.strptime(str(stock_data.iloc[i,0]), '%Y-%m-%d %H:%M:%S').strftime('%m/%d/%y')

In [7]:
for i in range(news_data.shape[0]-1):
    
    p = datetime.strptime(news_data.iloc[i,news_data.shape[1]-1],'%m/%d/%y')
    
    if(p.weekday() == 4):
        #print(p)
        
        x =   (p).strftime('%m/%d/%y')
        friday = news_data[news_data.iloc[:,news_data.shape[1]-1]==x].iloc[0,0:news_data.shape[1]-1]
        
        y =   (p + timedelta(days=1)).strftime('%m/%d/%y')
        saturday = news_data[news_data.iloc[:,news_data.shape[1]-1]==y].iloc[0,0:news_data.shape[1]-1]
        
        z =   (p + timedelta(days=1)).strftime('%m/%d/%y')
        sunday = news_data[news_data.iloc[:,news_data.shape[1]-1]==z].iloc[0,0:news_data.shape[1]-1]
        
        friday = ((friday + saturday + sunday))
        
        news_data[news_data.iloc[:,news_data.shape[1]-1]==x].iloc[0,0:news_data.shape[1]-1] = friday

C:\Users\prash\Anaconda3\lib\site-packages\pandas\core\indexing.py:494: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


IndexError: single positional indexer is out-of-bounds

### Creating the final dataset

In [7]:
df = []
Y = []
for i in range(stock_data.shape[0]-1):
    for j in range(news_data.shape[0]):
        
        if(news_data.iloc[j,-1]==stock_data.iloc[i,0]):
            
            #print(news_data.iloc[j,-1])
            
            z = list(stock_data.iloc[i,:]) + list(news_data.iloc[j,:-1])
            
            #Y.append(stock_data.iloc[i+1,2])
            
            #Y.append(1 if (stock_data.iloc[i+1,2] >= stock_data.iloc[i,2]) else 0)
            
            Y.append(1 if (stock_data.iloc[i+1,2] >= stock_data.iloc[i,2]) else 0)
            
            df.append(z)
        

In [8]:
df = pd.DataFrame(df)
df.shape

(253, 24)

In [9]:
df

0         1         2          3         4         5         6   \
0    01/01/19  10923.60  10862.55  159404542  10807.10  10881.70  10913.20   
1    01/02/19  10895.35  10910.10  309665939  10735.05  10868.85  10881.70   
2    01/03/19  10814.05  10792.50  286241745  10661.25  10796.80  10868.85   
3    01/04/19  10741.05  10672.25  296596655  10628.65  10699.70  10796.80   
4    01/07/19  10835.95  10727.35  269371080  10750.15  10804.85  10699.70   
..        ...       ...       ...        ...       ...       ...       ...   
248  01/30/20  12150.30  12129.50  538138743  12010.60  12147.75  12114.90   
249  01/31/20  12103.55  12035.80  771278258  11945.85  12100.40  12147.75   
250  02/03/20  11749.85  11661.85  669815788  11614.50  11627.45  12100.40   
251  02/04/20  11986.15  11707.90  560430291  11783.40  11786.25  11627.45   
252  02/05/20  12098.15  11979.65  758032580  11953.35  12005.85  11786.25   

           7         8         9   ...        14        15        16  \
0    0.000070  0.000140  0.000140  ...  0.000244  0.000210  0.000070   
1    0.000175  0.000105  0.000175  ...  0.000244  0.000175  0.000000   
2    0.000140  0.000140  0.000140  ...  0.000035  0.000035  0.000070   
3    0.000175  0.000070  0.000140  ...  0.000210  0.000140  0.000070   
4    0.000105  0.000035  0.000279  ...  0.000244  0.000105  0.000035   
..        ...       ...       ...  ...       ...       ...       ...   
248  0.000105  0.000000  0.000140  ...  0.000314  0.000070  0.000070   
249  0.000175  0.000035  0.000210  ...  0.000175  0.000035  0.000140   
250  0.000000  0.000175  0.000384  ...  0.000698  0.000000  0.000000   
251  0.000105  0.000035  0.000524  ...  0.000244  0.000000  0.000210   
252  0.000070  0.000070  0.000349  ...  0.000314  0.000035  0.000105   

           17        18        19        20        21        22        23  
0    0.000175  0.000070  0.000175  0.000000  0.000070  0.000175  0.000140  
1    0.000244  0.000070  0.000140  0.000070  0.000070  0.000279  0.000140  
2    0.000349  0.000210  0.000384  0.000070  0.000175  0.000314  0.000175  
3    0.000140  0.000279  0.000210  0.000070  0.000105  0.000244  0.000105  
4    0.000105  0.000279  0.000105  0.000105  0.000035  0.000175  0.000244  
..        ...       ...       ...       ...       ...       ...       ...  
248  0.000419  0.000105  0.000105  0.000175  0.000035  0.000175  0.000140  
249  0.000594  0.000140  0.000140  0.000035  0.000035  0.000105  0.000175  
250  0.000419  0.000070  0.000210  0.000105  0.000000  0.000105  0.000070  
251  0.000210  0.000035  0.000070  0.000035  0.000035  0.000140  0.000035  
252  0.000419  0.000000  0.000070  0.000000  0.000035  0.000105  0.000140  

[253 rows x 24 columns]

In [10]:
df.iloc[:,0] = pd.to_datetime(df.iloc[:,0])
df

0         1         2          3         4         5         6   \
0   2019-01-01  10923.60  10862.55  159404542  10807.10  10881.70  10913.20   
1   2019-01-02  10895.35  10910.10  309665939  10735.05  10868.85  10881.70   
2   2019-01-03  10814.05  10792.50  286241745  10661.25  10796.80  10868.85   
3   2019-01-04  10741.05  10672.25  296596655  10628.65  10699.70  10796.80   
4   2019-01-07  10835.95  10727.35  269371080  10750.15  10804.85  10699.70   
..         ...       ...       ...        ...       ...       ...       ...   
248 2020-01-30  12150.30  12129.50  538138743  12010.60  12147.75  12114.90   
249 2020-01-31  12103.55  12035.80  771278258  11945.85  12100.40  12147.75   
250 2020-02-03  11749.85  11661.85  669815788  11614.50  11627.45  12100.40   
251 2020-02-04  11986.15  11707.90  560430291  11783.40  11786.25  11627.45   
252 2020-02-05  12098.15  11979.65  758032580  11953.35  12005.85  11786.25   

           7         8         9   ...        14        15        16  \
0    0.000070  0.000140  0.000140  ...  0.000244  0.000210  0.000070   
1    0.000175  0.000105  0.000175  ...  0.000244  0.000175  0.000000   
2    0.000140  0.000140  0.000140  ...  0.000035  0.000035  0.000070   
3    0.000175  0.000070  0.000140  ...  0.000210  0.000140  0.000070   
4    0.000105  0.000035  0.000279  ...  0.000244  0.000105  0.000035   
..        ...       ...       ...  ...       ...       ...       ...   
248  0.000105  0.000000  0.000140  ...  0.000314  0.000070  0.000070   
249  0.000175  0.000035  0.000210  ...  0.000175  0.000035  0.000140   
250  0.000000  0.000175  0.000384  ...  0.000698  0.000000  0.000000   
251  0.000105  0.000035  0.000524  ...  0.000244  0.000000  0.000210   
252  0.000070  0.000070  0.000349  ...  0.000314  0.000035  0.000105   

           17        18        19        20        21        22        23  
0    0.000175  0.000070  0.000175  0.000000  0.000070  0.000175  0.000140  
1    0.000244  0.000070  0.000140  0.000070  0.000070  0.000279  0.000140  
2    0.000349  0.000210  0.000384  0.000070  0.000175  0.000314  0.000175  
3    0.000140  0.000279  0.000210  0.000070  0.000105  0.000244  0.000105  
4    0.000105  0.000279  0.000105  0.000105  0.000035  0.000175  0.000244  
..        ...       ...       ...       ...       ...       ...       ...  
248  0.000419  0.000105  0.000105  0.000175  0.000035  0.000175  0.000140  
249  0.000594  0.000140  0.000140  0.000035  0.000035  0.000105  0.000175  
250  0.000419  0.000070  0.000210  0.000105  0.000000  0.000105  0.000070  
251  0.000210  0.000035  0.000070  0.000035  0.000035  0.000140  0.000035  
252  0.000419  0.000000  0.000070  0.000000  0.000035  0.000105  0.000140  

[253 rows x 24 columns]

In [11]:
#df['Day'] = pd.DatetimeIndex(df.iloc[:,0]).day % 7
#df['Month'] = pd.DatetimeIndex(df.iloc[:,0]).month
#df['Year'] = pd.DatetimeIndex(df.iloc[:,0]).year

In [12]:
pd.DataFrame(Y).head(5)

0
0  1
1  0
2  0
3  1
4  1

In [13]:
from sklearn import preprocessing

In [14]:
#min_max_scaler = preprocessing.MinMaxScaler()
#X = min_max_scaler.fit_transform(X)
#Y = min_max_scaler.fit_transform(Y)

In [15]:
X = np.array(df.iloc[:,1:])

Y = np.array(Y)
Y = Y.reshape(Y.size,1)


#n_train_hours = int(0.90*X.shape[0])
n_train_hours = 122

train_X = X[:n_train_hours, :]
train_y = Y[:n_train_hours, :]
test_X = X[n_train_hours:, :]
test_y = Y[n_train_hours:, :]


print(train_X.shape, train_y.shape, test_X.shape, test_y.shape)

# Feature Scaling
from sklearn.preprocessing import StandardScaler

sc = StandardScaler()
train_X = sc.fit_transform(train_X)
test_X = sc.transform(test_X)


from sklearn.ensemble import RandomForestRegressor

regressor = XGBClassifier()
regressor.fit(train_X, train_y)
y_pred = regressor.predict(test_X)

s = 0
for i in range(len(test_y)):
    if((y_pred>=0.5).astype(int)[i]==test_y[i]):
        s += 1
        
        
acc = (s/len(test_y))*100
acc

(122, 23) (122, 1) (131, 23) (131, 1)


C:\Users\prash\Anaconda3\lib\site-packages\sklearn\ensemble\weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will resu

57.25190839694656

In [16]:
len(X)

253

In [37]:
X = np.array(df.iloc[:,1:])

Y = np.array(Y)
Y = Y.reshape(Y.size,1)

acc = []

for j in range(20,len(X),10):
    
    n_train_hours = j
    
    
    s=0
    z = 0

    for i in range(len(X) - n_train_hours - 1):

        #print(i)

        train_X = X[i:(i+ n_train_hours + 1), :]
        train_y = Y[i:(i+ n_train_hours + 1), :]
        test_X = X[(i+ n_train_hours + 1):(i+ n_train_hours + 3), :]
        test_y = Y[(i+ n_train_hours + 1):(i+ n_train_hours + 3), :]


        mean = train_X.mean(axis=0)
        train_X -= mean
        std = train_X.std(axis=0)
        train_X /= std


        mean = test_X.mean(axis=0)
        test_X -= mean
        std = test_X.std(axis=0)
        test_X /= std

        regressor = XGBClassifier()
        regressor.fit(train_X, train_y)
        y_pred = regressor.predict(test_X)

        z += 1

        if((y_pred>=0.5).astype(int)[0]==test_y[0]):
            s += 1


    #print(s)

    #print(z)

    acc.append((s/z)*100)

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will 

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

...

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will 

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

In [43]:
X = np.array(df.iloc[:,1:7])

Y = np.array(Y)
Y = Y.reshape(Y.size,1)

acc1 = []

for j in range(20,len(X),10):
    
    n_train_hours = j
    
    
    s=0
    z = 0

    for i in range(len(X) - n_train_hours - 1):

        #print(i)

        train_X = X[i:(i+ n_train_hours + 1), :]
        train_y = Y[i:(i+ n_train_hours + 1), :]
        test_X = X[(i+ n_train_hours + 1):(i+ n_train_hours + 3), :]
        test_y = Y[(i+ n_train_hours + 1):(i+ n_train_hours + 3), :]


        mean = train_X.mean(axis=0)
        train_X -= mean
        std = train_X.std(axis=0)
        train_X /= std


        mean = test_X.mean(axis=0)
        test_X -= mean
        std = test_X.std(axis=0)
        test_X /= std

        regressor = XGBClassifier()
        regressor.fit(train_X, train_y)
        y_pred = regressor.predict(test_X)

        z += 1

        if((y_pred>=0.5).astype(int)[0]==test_y[0]):
            s += 1


    #print(s)

    #print(z)

    acc1.append((s/z)*100)

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will 

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will 

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will 

...

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will 

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will 

C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:128: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
C:\Users\prash\Anaconda3\lib\site-packages\sklearn\preprocessing\label.py:95: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y

In [39]:
acc

[53.44827586206896,
 53.153153153153156,
 51.41509433962265,
 54.95049504950495,
 52.604166666666664,
 53.84615384615385,
 55.23255813953488,
 51.23456790123457,
 53.289473684210535,
 54.22535211267606,
 53.78787878787878,
 61.47540983606557,
 61.60714285714286,
 60.78431372549019,
 59.78260869565217,
 60.97560975609756,
 63.888888888888886,
 61.29032258064516,
 55.769230769230774,
 54.761904761904766,
 59.375,
 54.54545454545454,
 50.0,
 100.0]

In [40]:
acc1

[52.1551724137931,
 51.35135135135135,
 52.358490566037744,
 55.44554455445545,
 54.6875,
 53.84615384615385,
 55.23255813953488,
 51.23456790123457,
 53.289473684210535,
 54.22535211267606,
 53.78787878787878,
 61.47540983606557,
 61.60714285714286,
 60.78431372549019,
 59.78260869565217,
 60.97560975609756,
 63.888888888888886,
 61.29032258064516,
 55.769230769230774,
 54.761904761904766,
 59.375,
 54.54545454545454,
 50.0,
 100.0]

In [41]:
plt.plot(range(20,len(X),10),acc1,c='blue')
plt.plot(range(20,len(X),10),acc,c='red')